In [1]:
import torch
from tqdm.auto import tqdm

from point_e.diffusion.configs import DIFFUSION_CONFIGS, diffusion_from_config
from point_e.diffusion.sampler import PointCloudSampler
from point_e.models.download import load_checkpoint
from point_e.models.configs import MODEL_CONFIGS, model_from_config
from point_e.util.plotting import plot_point_cloud

In [2]:
device = torch.device('cuda')

print('creating base model...')
base_name = 'base40M-textvec'
base_model = model_from_config(MODEL_CONFIGS[base_name], device)
base_model.eval()
base_diffusion = diffusion_from_config(DIFFUSION_CONFIGS[base_name])

print('creating upsample model...')
upsampler_model = model_from_config(MODEL_CONFIGS['upsample'], device)
upsampler_model.eval()
upsampler_diffusion = diffusion_from_config(DIFFUSION_CONFIGS['upsample'])

print('downloading base checkpoint...')
base_model.load_state_dict(load_checkpoint(base_name, device))

print('downloading upsampler checkpoint...')
upsampler_model.load_state_dict(load_checkpoint('upsample', device))

creating base model...
creating upsample model...
downloading base checkpoint...
downloading upsampler checkpoint...


<All keys matched successfully>

In [3]:
sampler = PointCloudSampler(
    device=device,
    models=[base_model, upsampler_model],
    diffusions=[base_diffusion, upsampler_diffusion],
    num_points=[1024, 4096 - 1024],
    aux_channels=['R', 'G', 'B'],
    guidance_scale=[3.0, 0.0],
    model_kwargs_key_filter=('texts', ''), # Do not condition the upsampler at all
)

In [4]:
# Set a prompt to condition on.
prompt = 'A bluebird mid-flight'

# Produce a sample from the model.
samples = None
for x in tqdm(sampler.sample_batch_progressive(batch_size=1, model_kwargs=dict(texts=[prompt]))):
    samples = x

0it [00:00, ?it/s]

In [ ]:
pc = sampler.output_to_point_clouds(samples)[0]
fig = plot_point_cloud(pc, grid_size=2)

In [11]:
pc = sampler.output_to_point_clouds(samples)[0]
with open('example_data/blue_bird.ply','wb') as f:
    pc.write_ply(f)
#pc.save('example_data/blue_bird.npz')

In [8]:
pc = sampler.output_to_point_clouds(samples)[0]
print(pc)

PointCloud(coords=array([[ 0.2723148 ,  0.15381676,  0.00761994],
       [-0.25651944,  0.18783031,  0.0212175 ],
       [ 0.12061116,  0.05600073,  0.00907129],
       ...,
       [-0.00173135, -0.13978139,  0.00305715],
       [-0.00342358,  0.15288702, -0.02027267],
       [-0.116662  ,  0.14891137,  0.02732913]], dtype=float32), channels={'R': array([0.03137255, 0.02745098, 0.02745098, ..., 0.03529412, 0.03529412,
       0.03529412], dtype=float32), 'G': array([0.00392157, 0.        , 0.        , ..., 0.01176471, 0.00784314,
       0.01176471], dtype=float32), 'B': array([1., 1., 1., ..., 1., 1., 1.], dtype=float32)})
